In [214]:
import pandas as pd
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np

def read_metrics(file_path):
    metrics = pd.read_csv(file_path)
    metrics['total_time_us'] = metrics['total_time_us'] - metrics['inference_start']
    metrics['non_max_suppression'] = metrics['non_max_suppression'] - metrics['model']
    metrics['model'] = metrics['model'] - metrics['inference_start']

    metrics['inference_start'] = metrics['inference_start'] - metrics['inference_start'][0]

    metrics.iloc(1)[:4] = metrics.iloc(1)[:4] // 1000
    metrics = metrics[metrics['model'] < metrics['model'].quantile(0.99)]
    metrics['model_per_frame'] = metrics['model'] // metrics['batch_size']
    metrics['total_per_frame'] = metrics['total_time_us'] // metrics['batch_size']
    metrics['fps'] = 1 / (metrics['total_per_frame'] / 1_000_000)
    return metrics

def create_histograms(metrics_list, name_list, title, metric_name):
    fig = make_subplots(rows=len(metrics_list), cols=1, shared_xaxes=True, vertical_spacing=0.02)
    for idx, (metric, name) in enumerate(zip(metrics_list, name_list)):
        fig.add_histogram(x=metric[metric_name], row=idx+1, col=1, nbinsx=200, name=name)
        fig.add_vline(x=np.median(metric[metric_name]), row=idx+1, col=1, annotation_text=round(np.median(metric[metric_name]), 2), annotation_bgcolor='rgba(255,255,255,0.5)', annotation_xshift=3)

    fig.update_layout(height=100*len(metrics_list)+150, title=title)
    return fig

def create_ecdfs(metrics_list, name_list, title, metric_name):
    fig = go.Figure()
    for metric, name in zip(metrics_list, name_list):
        data = metric[metric_name]
        fig.add_scatter(x=np.unique(data), y=ecdf(data)(np.unique(data)), line_shape='hv', name=name)
    fig.update_layout(height=400, title=title)
    return fig

def ecdf(x):
    x = np.sort(x)
    def result(v):
        return np.searchsorted(x, v, side='right') / x.size
    return result
    

In [215]:
files = [
    'remote/metrics_yolov8n_b1_cpu_6t.csv',
    'remote/metrics_yolov8n_b1_cpu_12t.csv',
    'remote/metrics_yolov8n_b1_cpu_24t.csv',
    'remote/metrics_yolov8n_b1_cpu_36t.csv',
    'remote/metrics_yolov8n_b1_cpu_48t.csv',
    'remote/metrics_yolov8n_b1_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 1', 'fps').show()

files = [
    'remote/metrics_yolov8n_b3_cpu_6t.csv',
    'remote/metrics_yolov8n_b3_cpu_12t.csv',
    'remote/metrics_yolov8n_b3_cpu_24t.csv',
    'remote/metrics_yolov8n_b3_cpu_36t.csv',
    'remote/metrics_yolov8n_b3_cpu_48t.csv',
    'remote/metrics_yolov8n_b3_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 3', 'fps').show()

files = [
    'remote/metrics_yolov8n_b5_cpu_6t.csv',
    'remote/metrics_yolov8n_b5_cpu_12t.csv',
    'remote/metrics_yolov8n_b5_cpu_24t.csv',
    'remote/metrics_yolov8n_b5_cpu_36t.csv',
    'remote/metrics_yolov8n_b5_cpu_48t.csv',
    'remote/metrics_yolov8n_b5_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 5', 'fps').show()

files = [
    'remote/metrics_yolov8n_b10_cpu_6t.csv',
    'remote/metrics_yolov8n_b10_cpu_12t.csv',
    'remote/metrics_yolov8n_b10_cpu_24t.csv',
    'remote/metrics_yolov8n_b10_cpu_36t.csv',
    'remote/metrics_yolov8n_b10_cpu_48t.csv',
    'remote/metrics_yolov8n_b10_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 10', 'fps').show()

files = [
    'remote/metrics_yolov8n_b20_cpu_6t.csv',
    'remote/metrics_yolov8n_b20_cpu_12t.csv',
    'remote/metrics_yolov8n_b20_cpu_24t.csv',
    'remote/metrics_yolov8n_b20_cpu_36t.csv',
    'remote/metrics_yolov8n_b20_cpu_48t.csv',
    'remote/metrics_yolov8n_b20_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 20', 'fps').show()

files = [
    'remote/metrics_yolov8n_b40_cpu_6t.csv',
    'remote/metrics_yolov8n_b40_cpu_12t.csv',
    'remote/metrics_yolov8n_b40_cpu_24t.csv',
    'remote/metrics_yolov8n_b40_cpu_36t.csv',
    'remote/metrics_yolov8n_b40_cpu_48t.csv',
    'remote/metrics_yolov8n_b40_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Thread scaling - Batch size 40', 'fps').show()

In [187]:
files = [
    'remote/metrics_yolov8n_b1_cpu_6t.csv',
    'remote/metrics_yolov8n_b3_cpu_6t.csv',
    'remote/metrics_yolov8n_b5_cpu_6t.csv',
    'remote/metrics_yolov8n_b10_cpu_6t.csv',
    'remote/metrics_yolov8n_b20_cpu_6t.csv',
    'remote/metrics_yolov8n_b40_cpu_6t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 6 Threads', 'fps').show()

files = [
    'remote/metrics_yolov8n_b1_cpu_12t.csv',
    'remote/metrics_yolov8n_b3_cpu_12t.csv',
    'remote/metrics_yolov8n_b5_cpu_12t.csv',
    'remote/metrics_yolov8n_b10_cpu_12t.csv',
    'remote/metrics_yolov8n_b20_cpu_12t.csv',
    'remote/metrics_yolov8n_b40_cpu_12t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 12 Threads', 'fps').show()

files = [
    'remote/metrics_yolov8n_b1_cpu_24t.csv',
    'remote/metrics_yolov8n_b3_cpu_24t.csv',
    'remote/metrics_yolov8n_b5_cpu_24t.csv',
    'remote/metrics_yolov8n_b10_cpu_24t.csv',
    'remote/metrics_yolov8n_b20_cpu_24t.csv',
    'remote/metrics_yolov8n_b40_cpu_24t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 24 Threads', 'fps').show()

files = [
    'remote/metrics_yolov8n_b1_cpu_36t.csv',
    'remote/metrics_yolov8n_b3_cpu_36t.csv',
    'remote/metrics_yolov8n_b5_cpu_36t.csv',
    'remote/metrics_yolov8n_b10_cpu_36t.csv',
    'remote/metrics_yolov8n_b20_cpu_36t.csv',
    'remote/metrics_yolov8n_b40_cpu_36t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 36 Threads', 'fps').show()

files = [
    'remote/metrics_yolov8n_b1_cpu_48t.csv',
    'remote/metrics_yolov8n_b3_cpu_48t.csv',
    'remote/metrics_yolov8n_b5_cpu_48t.csv',
    'remote/metrics_yolov8n_b10_cpu_48t.csv',
    'remote/metrics_yolov8n_b20_cpu_48t.csv',
    'remote/metrics_yolov8n_b40_cpu_48t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 48 Threads', 'fps').show()

files = [
    'remote/metrics_yolov8n_b1_cpu_112t.csv',
    'remote/metrics_yolov8n_b3_cpu_112t.csv',
    'remote/metrics_yolov8n_b5_cpu_112t.csv',
    'remote/metrics_yolov8n_b10_cpu_112t.csv',
    'remote/metrics_yolov8n_b20_cpu_112t.csv',
    'remote/metrics_yolov8n_b40_cpu_112t.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Batch scaling - 112 Threads', 'fps').show()

In [180]:
files = [
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_1p_1.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Parallel scaling - 1 process', 'fps').show()

files = [
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_2p_1.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_2p_2.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Parallel scaling - 2 processes', 'fps').show()

files = [
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_3p_1.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_3p_2.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_3p_3.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Parallel scaling - 3 processes', 'fps').show()

files = [
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_4p_1.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_4p_2.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_4p_3.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_4p_4.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Parallel scaling - 4 processes', 'fps').show()

In [150]:
files = [
    'remote_parallel/metrics_yolov8n_b5_cpu_48t_2p_1c.csv',
    'remote_parallel/metrics_yolov8n_b5_cpu_48t_2p_2c.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_2p_1c.csv',
    'remote_parallel/metrics_yolov8n_b10_cpu_48t_2p_2c.csv',
    'remote_parallel/metrics_yolov8n_b20_cpu_48t_2p_1c.csv',
    'remote_parallel/metrics_yolov8n_b20_cpu_48t_2p_2c.csv',
]

create_histograms([read_metrics(f) for f in files], files, 'Comparing one process on CPU 0 (1c) and one on CPU 1 (2c)').show()